# Восстановление пробелов в тексте

В этом ноутбуке мы решаем задачу: дан текст без пробелов, нужно автоматически восстановить их.
Подход:

* собираем данные из Википедии и Ленты (чистый литературный текст) и Авито (реальные объявления с ошибками);

* готовим пары «слитный текст → правильный текст»;

* строим символьный словарь и датасет;

* обучаем BiLSTM-модель в два этапа (сначала на чистом тексте, потом на смеси с Авито);

* подбираем порог для вставки пробелов;

* используем постпроцессинг (морфология, бренды, пунктуация), чтобы улучшить результат;

* получаем финальные предсказания и формируем submission.csv.

### Установка зависимостей

In [1]:
!pip -q install "transformers>=4.42" "datasets>=2.19" accelerate sentencepiece pyarrow kagglehub wikiextractor torch torchtext pymorphy3
!pip -q install wordfreq

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 46.4/46.4 kB 4.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 2.0/2.0 MB 89.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 54.1/54.1 kB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.4/8.4 MB 147.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 56.8/56.8 MB 17.7 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.8/44.8 kB 3.5 MB/s eta 0:00:00


### Импорты и базовые настройки
seed = 42 зафиксирован для воспроизводимости полученных результатов при повторном обучении/оценке

In [2]:
import os, re, glob, json, random, string, math, gc
from functools import lru_cache
from typing import List, Tuple

import numpy as np
import pandas as pd
from tqdm.auto import tqdm

import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.utils.data import Dataset, DataLoader

from datasets import load_dataset, concatenate_datasets
import kagglehub

from wordfreq import zipf_frequency
import pymorphy3

seed = 42
os.environ["PYTHONHASHSEED"] = str(seed)
random.seed(seed)
np.random.seed(seed)
torch.manual_seed(seed)
torch.cuda.manual_seed_all(seed)

device = "cuda" if torch.cuda.is_available() else "cpu"
device

'cuda'

### Текстовые утилиты и фильтры

* norm_spaces — нормализует пробелы: заменяет нестандартные
символы пробела на обычный и сжимает повторяющиеся пробелы в один. Нужно, чтобы текст был чистым и единообразным.

* filter_chars — оставляет только допустимые буквы, цифры и основные знаки препинания, удаляя всё остальное. Нужно для очистки данных от мусора (эмодзи, спецсимволов).

* prepare_line — применяет фильтрацию и нормализацию пробелов, а потом выбрасывает слишком короткие или длинные строки. Нужно, чтобы в выборке оставались только адекватные примеры для обучения.

* remove_spaces — убирает все пробелы из строки. Нужно, чтобы получить «слитный» текст — вход модели.

* positions_from_spaced — вычисляет индексы, где стоят пробелы (считая только символы без пробелов). Нужно, чтобы иметь разметку правильных позиций пробелов.

* make_pairs — из списка текстов формирует пары (слитный_текст, нормальный_текст) для строк подходящей длины. Нужно, чтобы подготовить обучающие примеры.

* f1_pair — считает F1-метрику между предсказанными и истинными позициями пробелов. Нужно, чтобы измерять качество модели (баланс точности и полноты).

In [3]:
def norm_spaces(t: str) -> str:
    return re.sub(r"\s+", " ", t.replace("\u00A0"," ").replace("\u200b"," ").replace("\t"," ")).strip()

def filter_chars(text: str) -> str:
    allowed = set(
        string.ascii_letters + string.digits +
        "абвгдеёжзийклмнопрстуфхцчшщьыъэюя" +
        "АБВГДЕЁЖЗИЙКЛМНОПРСТУФХЦЧШЩЬЫЪЭЮЯ" +
        " .,:;!?-—–()«»„“…/%#\"'+"
    )
    return "".join(ch for ch in text if ch in allowed or ch.isspace())

def prepare_line(text: str, min_len=15, max_len=160) -> str:
    text = filter_chars(text); text = norm_spaces(text)
    return text if (min_len <= len(text) <= max_len) else ""

def remove_spaces(s: str) -> str:
    return s.replace(" ", "")

def positions_from_spaced(spaced: str):
    pos, c = [], 0
    for ch in spaced:
        if ch == " ":
            pos.append(c)
        else:
            c += 1
    return pos

def make_pairs(texts, min_len=15, max_len=160):
    pairs = []
    for t in texts:
        if not t:
            continue
        s = remove_spaces(t)
        if min_len <= len(s) <= max_len:
            pairs.append((s, t))
    return pairs

def f1_pair(pred_positions, true_positions):
    ps, ts = set(pred_positions), set(true_positions)
    if not ps and not ts: return 1.0
    if not ps or not ts:  return 0.0
    inter=len(ps&ts); p=inter/len(ps); r=inter/len(ts)
    return 0.0 if p+r==0 else 2*p*r/(p+r)



### Загрузка данных (Avito, Lenta, Wikipedia)

Формируем обучающую выборку из трёх разных источников:

Грамотная литература:

* Википедия — самая свежая версия русской Википедии (август 2025). Это максимально формальный стиль, хороший источник правильного языка.

* Лента.ру — новости. Здесь стиль менее формальный, чем у Википедии, но при этом язык остаётся литературным. Такой корпус даёт модели больше разнообразия, ближе к разговорному, но без грубых ошибок.

Доменные данные:

* Avito — данные с Avito ML Cup. Здесь встречаются именно такие тексты, для которых мы хотим обучить модель: объявления с опечатками, слитным написанием и пропущенными пробелами. Это приближает выборку к реальной задаче.

In [4]:
avito_path = kagglehub.dataset_download("antonoof/avito-data")

def load_avito_base_description(folder: str, cap: int = 150_000):
    files = sorted(glob.glob(os.path.join(folder, "**", "*.parquet"), recursive=True))
    seen = set(); out = []
    for fp in tqdm(files, desc="read parquet"):
        try:
            df = pd.read_parquet(fp, columns=["base_description"])
        except Exception as e:
            print("skip", fp, "->", e); continue
        for t in df["base_description"].dropna().astype(str):
            t = prepare_line(t)
            if not t: continue
            k = remove_spaces(t).lower()
            if k in seen: continue
            seen.add(k); out.append(t)
            if len(out) >= cap: break
        if len(out) >= cap: break
    random.Random(seed).shuffle(out)
    return out

avito_texts = load_avito_base_description(avito_path, cap=150_000)
len(avito_texts), avito_texts[:3]

Using Colab cache for faster access to the 'avito-data' dataset.


read parquet:   0%|          | 0/6 [00:00<?, ?it/s]

(150000,
 ['В обычном paбочем cоcтоянии, нa меcте можно пpовеpить. 88 чиповый.',
  'Пpодaм готовую кapтину по номеpaм. Рaзмеp 40х50',
  'Чёpное плaтье откpытой cпиной. Подчеpкнёт вaшу индивидуaльноcть плaтье новое. Рaзмеpы: SML , мaломеpит.'])

In [5]:
lenta_path = kagglehub.dataset_download("yutkin/corpus-of-russian-news-articles-from-lenta")

def read_lenta_texts_from_kaggle(root: str, limit=300_000):
    csvs = sorted(glob.glob(os.path.join(root, "**/*.csv"), recursive=True))
    seen = set(); out = []
    for csv in csvs:
        for chunk in pd.read_csv(csv, usecols=["text", "title"], chunksize=50_000):
            for t in chunk["text"].dropna().astype(str):
                for sent in re.split(r"[.!?]|\n", t):
                    s = prepare_line(sent)
                    if not s:
                        continue
                    k = remove_spaces(s).lower()
                    if k in seen:
                        continue
                    seen.add(k); out.append(s)
                    if len(out) >= limit:
                        random.Random(seed).shuffle(out)
                        return out
    random.Random(seed).shuffle(out)
    return out

lenta_texts = read_lenta_texts_from_kaggle(lenta_path, limit=300_000)
len(lenta_texts), lenta_texts[:3]

Using Colab cache for faster access to the 'corpus-of-russian-news-articles-from-lenta' dataset.


(300000,
 ['Разборку самолета по контракту с Пентагоном осуществляет техническая группа из 6 сотрудников американской аэрокосмической корпорации Lockheed Martin',
  'Ястржембский снова подчеркнул, что корреспондент радио "Свобода" жив и здоров, сославшись при этом на данные радиоперехватов',
  'Одобренный в субботу документ будет дорабатываться в течение месяца, после чего поступит на подпись к премьер-министру Михаилу Касьянову'])

In [6]:
def load_ruwiki_sentences_from_hf(limit=300_000, seed=seed):
    seen, out = set(), []
    ds = load_dataset("omarkamali/wikipedia-monthly", "20250801.ru", split="train")
    for ex in ds:
        text = ex.get("text", "")
        for sent in re.split(r"[.!?]|\n", text):
            s = prepare_line(sent)
            if not s:
                continue
            k = remove_spaces(s).lower()
            if k in seen:
                continue
            seen.add(k); out.append(s)
            if len(out) >= limit:
                random.Random(seed).shuffle(out)
                return out
    random.Random(seed).shuffle(out)
    return out

wiki_texts = load_ruwiki_sentences_from_hf(limit=300_000)
len(wiki_texts), wiki_texts[:3]

/usr/local/lib/python3.12/dist-packages/huggingface_hub/utils/_auth.py:94: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


README.md: 0.00B [00:00, ?B/s]

Resolving data files:   0%|          | 0/412 [00:00<?, ?it/s]

20250801/ru/train/train_part_000.parquet:   0%|          | 0.00/61.7M [00:00<?, ?B/s]

20250801/ru/train/train_part_001.parquet:   0%|          | 0.00/59.5M [00:00<?, ?B/s]

...

Generating 1000 split: 0 examples [00:00, ? examples/s]

Generating 5000 split: 0 examples [00:00, ? examples/s]

Generating 10000 split: 0 examples [00:00, ? examples/s]

Loading dataset shards:   0%|          | 0/25 [00:00<?, ?it/s]

(300000,
 ['Часть манифестантов проникла на территорию дипмиссии, но выдворена силами безопасности',
  'В 1836 году началось освоение «Нового места» (территория современного Александровского сквера)',
  'Позже, в VIII—IX веках, появилось множество документов, собирающих генеалогические списки родов'])

Здесь мы объединяем тексты из Ленты и Википедии в один корпус (clean_texts), перемешиваем их и превращаем в пары (слитный_текст, нормальный_текст) с помощью make_pairs.
Аналогично формируем пары из текстов Авито.

In [7]:
clean_texts = (lenta_texts + wiki_texts)
random.Random(seed).shuffle(clean_texts)

clean_pairs = make_pairs(clean_texts)
avito_pairs = make_pairs(avito_texts)

print("clean_pairs:", len(clean_pairs), "avito_pairs:", len(avito_pairs))

clean_pairs: 594157 avito_pairs: 148722




### Дедупликация и разбиение данных

Функция dedup_split убирает дубликаты по тексту без пробелов и делит данные на три части: train (80%), dev (10%) и test (10%).
Это нужно, чтобы обучать и проверять модель на непересекающихся примерах и честно оценивать качество.

In [8]:
def dedup_split(pairs, seed=42):
    random.Random(seed).shuffle(pairs)
    seen = set(); uniq = []
    for src, tgt in pairs:
        k = remove_spaces(tgt).lower()
        if k in seen:
            continue
        seen.add(k)
        uniq.append((src, tgt))
    n = len(uniq)
    n_train = int(0.8*n); n_dev = int(0.1*n)
    return uniq[:n_train], uniq[n_train:n_train+n_dev], uniq[n_train+n_dev:]

train_avito, dev_avito, test_avito = dedup_split(avito_pairs, seed)

print("Avito split sizes:", len(train_avito), len(dev_avito), len(test_avito))
print("Clean for stage A:", len(clean_pairs))

Avito split sizes: 118977 14872 14873
Clean for stage A: 594157


### Словарь, датасет и батчинг с учётом длины

Функция build_vocab проходит по всем парам (слитный, нормальный) и собирает множество уникальных символов из слитных строк.
Затем создаётся словарь с индексами:

* 0 (для заполнения батчей),

* 1 (для неизвестных символов),

остальные символы нумеруются по алфавиту начиная с 2.

In [9]:
def build_vocab(pairs):
    chars = set()
    for s, t in pairs:
        chars |= set(s)
    vocab = {"<pad>": 0, "<unk>": 1}
    for i, ch in enumerate(sorted(chars), start=2):
        vocab[ch] = i
    return vocab

vocab = build_vocab(clean_pairs + avito_pairs)
print("Vocab size:", len(vocab))

Vocab size: 152


SpaceDataset

* хранит пары (слитный, нормальный) и словарь символов;

* в __getitem__ переводит слитный текст в индексы (x) и строит метки (y), где 1 значит «поставь пробел» на этой позиции, а 0 — «не ставь».

collate_batch

* собирает батч примеров разной длины;

* делает паддинг: x заполняется нулями (<pad>), y — значением -100 (чтобы лосс игнорировал паддинги);

* возвращает паддингованные тензоры и длины последовательностей.

In [10]:
class SpaceDataset(Dataset):
    def __init__(self, pairs, vocab):
        self.pairs = pairs
        self.vocab = vocab
    def __len__(self):
        return len(self.pairs)
    def __getitem__(self, idx):
        src, tgt = self.pairs[idx]
        x = [self.vocab.get(ch, self.vocab["<unk>"]) for ch in src]
        y = [0]*len(src)
        for pos in positions_from_spaced(tgt):
            if 0 <= pos < len(src):
                y[pos] = 1
        return torch.tensor(x, dtype=torch.long), torch.tensor(y, dtype=torch.long)

def collate_batch(batch):
    xs, ys = zip(*batch)
    lens = [len(x) for x in xs]
    max_len = max(lens)
    pad_x = torch.zeros(len(xs), max_len, dtype=torch.long)
    pad_y = torch.full((len(xs), max_len), -100, dtype=torch.long)
    for i, (x, y) in enumerate(zip(xs, ys)):
        L = len(x)
        pad_x[i, :L] = x
        pad_y[i, :L] = y
    return pad_x, pad_y, torch.tensor(lens, dtype=torch.long)

### Модель CharSeg (BiLSTM) с class weights, dropout, AdamW, clip-grad

compute_class_weights

* Считает баланс классов: сколько позиций с пробелами (pos) и без пробелов (neg).

* Возвращает веса для функции потерь: класс «пробел» получает больший вес, чтобы компенсировать его редкость.

CharSeg (BiLSTM-модель)

* Вход: индексы символов.

* Embedding: переводит символы в векторы фиксированной размерности.

* BiLSTM: двунаправленная рекуррентная сеть, которая учитывает контекст слева и справа.

* Dropout: регуляризация, чтобы модель не переобучалась.

* Linear: преобразует скрытые состояния в логиты для двух классов: «ставим пробел» / «не ставим пробел».

* Loss: если поданы целевые метки (y), считает cross_entropy с учётом весов и игнорированием паддингов.

In [11]:
def compute_class_weights(pairs):
    pos = neg = 0
    for src, tgt in pairs:
        p = len(positions_from_spaced(tgt))
        pos += p
        neg += len(src) - p
    w1 = neg / max(1, pos)
    w0 = 1.0
    return torch.tensor([w0, w1], dtype=torch.float)

class CharSeg(nn.Module):
    def __init__(self, vocab_size, emb_dim=192, hid_dim=384, num_layers=2, dropout=0.2):
        super().__init__()
        self.emb = nn.Embedding(vocab_size, emb_dim, padding_idx=0)
        self.lstm = nn.LSTM(emb_dim, hid_dim//2, num_layers=num_layers,
                            bidirectional=True, batch_first=True,
                            dropout=dropout if num_layers > 1 else 0.0)
        self.drop = nn.Dropout(dropout)
        self.fc = nn.Linear(hid_dim, 2)

    def forward(self, x, lengths, y=None, weight=None):
        emb = self.drop(self.emb(x))
        packed = nn.utils.rnn.pack_padded_sequence(emb, lengths.cpu(), batch_first=True, enforce_sorted=False)
        out, _ = self.lstm(packed)
        out, _ = nn.utils.rnn.pad_packed_sequence(out, batch_first=True, total_length=x.size(1))
        out = self.drop(out)
        logits = self.fc(out)
        loss = None
        if y is not None:
            loss = F.cross_entropy(logits.reshape(-1, 2), y.reshape(-1), weight=weight, ignore_index=-100)
        return loss, logits

Функция прогоняет слитный текст через модель, считает вероятность «пробел» для каждой позиции и вставляет пробелы там, где она выше порога tau.

In [12]:
@torch.no_grad()
def predict_spaces(model, text, vocab, tau=0.5):
    model.eval()
    x = torch.tensor([[vocab.get(ch, vocab["<unk>"]) for ch in text]], dtype=torch.long, device=device)
    lengths = torch.tensor([x.size(1)], dtype=torch.long, device=device)
    _, logits = model(x, lengths)
    probs = torch.softmax(logits, dim=-1)[0, :, 1].detach().cpu().numpy()
    out = []
    for i, ch in enumerate(text):
        if i > 0 and probs[i] >= tau:
            out.append(" ")
        out.append(ch)
    return "".join(out)

Обучение BiLSTM-модели

Функция train_stage_bilstm:

* готовит оптимизатор AdamW и DataLoader;

* запускает цикл по эпохам: считает loss, делает обратное распространение, ограничивает градиенты (clip_grad_norm_), обновляет веса;

* после каждой эпохи оценивает F1 на части dev-набора;

* сохраняет лучшую модель, а при нескольких неудачных эпохах подряд — останавливает обучение (early stopping).

In [13]:
def train_stage_bilstm(model, train_dataset, dev_pairs, vocab,
                       out_dir, epochs, lr, batch_size=64, patience=2, tau_eval=0.5,
                       class_weights=None):
    os.makedirs(out_dir, exist_ok=True)
    model.to(device)
    opt = torch.optim.AdamW(model.parameters(), lr=lr, weight_decay=0.01)
    loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True, collate_fn=collate_batch)
    best_f1, bad = -1.0, 0

    for ep in range(1, epochs+1):
        model.train(); tot=0.0
        for xb, yb, lb in loader:
            xb, yb, lb = xb.to(device), yb.to(device), lb.to(device)
            loss, _ = model(xb, lb, yb, class_weights.to(device) if class_weights is not None else None)
            opt.zero_grad(); loss.backward()
            nn.utils.clip_grad_norm_(model.parameters(), 1.0)
            opt.step()
            tot += float(loss)
        tr_loss = tot/len(loader)

        f1 = np.mean([
            f1_pair(positions_from_spaced(predict_spaces(model, src, vocab, tau_eval)),
                    positions_from_spaced(tgt))
            for src, tgt in dev_pairs[:2000]
        ])

        print(f"[{out_dir}] epoch {ep}/{epochs} loss={tr_loss:.4f} devF1={f1:.4f}")

        if f1 > best_f1:
            best_f1, bad = f1, 0
            torch.save({"model": model.state_dict(), "vocab": vocab}, os.path.join(out_dir, "best.pt"))
        else:
            bad += 1
            if bad >= patience:
                print("Early stop."); break

    ckpt = torch.load(os.path.join(out_dir, "best.pt"), map_location="cpu")
    model.load_state_dict(ckpt["model"])
    return model

### Постпроцессинг

В этом блоке собраны функции для «дочистки» результата модели:

Морфология и словарь:

* is_known_word — проверяет, есть ли слово в словаре pymorphy3.

* wscore, best_split_token, glue_with_freq — эвристики, чтобы разбить неизвестные слитные токены на более правдоподобные части.

Работа с брендами и сокращениями:

* fix_brands — восстанавливает написание известных брендов (по словарю).

* fix_abbreviations — убирает лишние пробелы внутри аббревиатур.

* fix_bu — приводит варианты «б/у» к единому виду.

Скрипты и цифры:

* split_script_changes — вставляет пробел между кириллицей/латиницей/цифрами (например, «iPhone12» → «iPhone 12»).

Частота и словарь:

* fix_with_dictionary — разбивает слова и склеивает их обратно с учётом частот и словаря, чтобы текст выглядел естественнее.

Пунктуация:

* fix_punctuation — чистит пробелы вокруг знаков препинания и тире.

Финальная сборка:

* postprocess_text последовательно применяет все исправления к строке.

In [14]:
morph = pymorphy3.MorphAnalyzer()
bad_tags = ("UNKN", "LATN", "PNCT", "NUMB", "ROMN")

@lru_cache(maxsize=200_000)
def morph_parses(w: str):
    return morph.parse(w)

def is_known_word(word: str) -> bool:
    w = word.strip().lower()
    if not w:
        return False
    for p in morph_parses(w):
        tag = str(p.tag)
        if getattr(p, "is_known", False) and not any(t in tag for t in bad_tags):
            return True
    return False

def load_brands(path="/content/brands.txt"):
    with open(path, "r", encoding="utf-8") as f:
        return {line.strip() for line in f if line.strip()}

brands = load_brands()

def normalize(s: str) -> str:
    return (s.lower().replace(" ", "").replace("-", "").replace("’", "").replace("'", "").replace(".", ""))

alnum_chars = "0-9A-Za-zА-Яа-яЁё"

def compile_brand_patterns(brands_set):
    patterns = []
    for brand in brands_set:
        b_norm = normalize(brand)
        if len(b_norm) < 2:
            continue
        core = "".join(f"{re.escape(ch)}\\s*" for ch in b_norm)
        rx = re.compile(rf"(?<![{alnum_chars}]){core}(?![{alnum_chars}])", re.IGNORECASE)
        patterns.append((brand, rx))
    return patterns

brand_patterns = compile_brand_patterns(brands)

def fix_brands(text: str) -> str:
    for brand, rx in brand_patterns:
        text = rx.sub(brand, text)
    return text

abbr_spaced = re.compile(r'\b(?:[А-ЯA-Z]\s*){2,}\b')

def fix_abbreviations(text: str) -> str:
    return abbr_spaced.sub(lambda m: re.sub(r'\s+', '', m.group(0)), text)

def fix_bu(text: str) -> str:
    return re.sub(r'\bб\s*/?\s*у\b', 'б/у', text, flags=re.IGNORECASE)

script_split_re = re.compile(
    r'(?<=[A-Za-z])(?=[А-Яа-яЁё])|'
    r'(?<=[А-Яа-яЁё])(?=[A-Za-z])|'
    r'(?<=[A-Za-zА-Яа-яЁё])(?=\d)|'
    r'(?<=\d)(?=[A-Za-zА-Яа-яЁё])'
)
def split_script_changes(text: str) -> str:
    return script_split_re.sub(" ", text)

cyrillic_re = re.compile(r'^[А-Яа-яЁё]+$')
latin_only_re = re.compile(r'^[A-Za-z0-9]+$')

def wscore(w: str) -> float:
    if not w:
        return -10.0
    if cyrillic_re.match(w) and len(w) <= 2:
        return -10.0
    freq = zipf_frequency(w.lower(), "ru")
    if freq == 0.0:
        return -5.0
    if len(w) <= 4 and freq < 3.0:
        return freq - 3.0
    if is_known_word(w) and len(w) >= 6:
        freq += 3.0
    return freq

def best_split_token(tok: str) -> list:
    tok = tok.strip()
    if not tok or latin_only_re.match(tok) or is_known_word(tok):
        return [tok] if tok else []
    n = len(tok)
    score = [float("-inf")] * (n + 1)
    back = [-1] * (n + 1)
    score[0] = 0.0
    max_chunk = 24
    for i in range(n):
        if score[i] == float("-inf"):
            continue
        for j in range(i + 1, min(n, i + max_chunk) + 1):
            w = tok[i:j]
            sc = score[i] + wscore(w)
            if sc > score[j]:
                score[j], back[j] = sc, i
    if score[n] == float("-inf"):
        return [tok]
    out, k = [], n
    while k > 0 and back[k] >= 0:
        i = back[k]
        out.append(tok[i:k])
        k = i
    return out[::-1]

def glue_with_freq(tokens: list) -> list:
    out, i, n = [], 0, len(tokens)
    while i < n:
        merged_best, best_freq, best_len = tokens[i], zipf_frequency(tokens[i].lower(), "ru"), 1
        for k in range(2, 5):
            if i + k <= n:
                merged = "".join(tokens[i:i+k])
                freq_m = zipf_frequency(merged.lower(), "ru")
                if freq_m > best_freq + 1.0 or (is_known_word(merged) and len(merged) >= 5):
                    merged_best, best_freq, best_len = merged, freq_m, k
        out.append(merged_best)
        i += best_len
    return out

def fix_with_dictionary(text: str) -> str:
    tokens = text.split()
    pieces = []
    for w in tokens:
        for sub in split_script_changes(w).split():
            pieces.extend(best_split_token(sub))
    return " ".join(glue_with_freq(pieces))

def fix_punctuation(text: str) -> str:
    text = re.sub(r"\s+([,?!:;.])", r"\1", text)
    text = re.sub(r"([,?!:;.])(?!\s|$)", r"\1 ", text)
    text = re.sub(r"\s*—\s*", " — ", text)
    text = re.sub(r"—\s*$", "—", text)
    return re.sub(r"\s{2,}", " ", text).strip()

def postprocess_text(text: str) -> str:
    text = split_script_changes(text)
    text = fix_brands(text)
    text = fix_abbreviations(text)
    text = fix_with_dictionary(text)
    text = fix_bu(text)
    return fix_punctuation(text)

### Обучение + калибровка τ

Подготовка датасетов для обучения

* ds_train_clean — корпус из Ленты и Википедии (чистый текст).

* ds_train_avito — корпус объявлений Авито (реальные «грязные» данные).

* ds_train_mix — смесь: все примеры Авито + случайная часть чистого корпуса (≈25% от размера Авито).

* weights_ce — вычисляются веса классов («пробел» / «не пробел») на основе смешанной выборки. Эти веса будут использоваться в функции потерь для балансировки классов.

In [15]:
ds_train_clean = SpaceDataset(clean_pairs, vocab)

n = len(train_avito)
ds_train_avito = SpaceDataset(train_avito, vocab)
mixed_pairs = train_avito + random.Random(seed).sample(clean_pairs, int(len(train_avito)*0.25))
ds_train_mix = SpaceDataset(mixed_pairs, vocab)

weights_ce = compute_class_weights(train_avito + random.Random(seed).sample(clean_pairs, min(100_000, len(clean_pairs))))
weights_ce

tensor([1.0000, 5.5472])

Двухэтапное обучение модели

* Стадия A (clean):

Модель обучается 2 эпохи на чистом корпусе (Лента + Википедия). Цель — дать модели «грамотную базу» и научить общим языковым закономерностям.

* Стадия B (mix):

Та же модель дообучается 5 эпох на смеси: Авито + часть чистого текста. Цель — адаптировать модель к реальным «грязным» данным (объявлениям), сохранив при этом знание нормального языка.

In [16]:
model = CharSeg(len(vocab))
model = train_stage_bilstm(model, ds_train_clean, dev_avito, vocab,
                           out_dir="/content/ckpt_A_clean",
                           epochs=2, lr=3e-3, batch_size=64,
                           class_weights=weights_ce, tau_eval=0.5)

model = train_stage_bilstm(model, ds_train_mix, dev_avito, vocab,
                           out_dir="/content/ckpt_B_mix",
                           epochs=5, lr=2e-3, batch_size=64,
                           class_weights=weights_ce, tau_eval=0.5)

/tmp/ipython-input-378380023.py:18: UserWarning: Converting a tensor with requires_grad=True to a scalar may lead to unexpected behavior.
Consider using tensor.detach() first. (Triggered internally at /pytorch/torch/csrc/autograd/generated/python_variable_methods.cpp:835.)
  tot += float(loss)


[/content/ckpt_A_clean] epoch 1/2 loss=0.0399 devF1=0.7474
[/content/ckpt_A_clean] epoch 2/2 loss=0.0252 devF1=0.7566
[/content/ckpt_B_mix] epoch 1/5 loss=0.0758 devF1=0.9271
[/content/ckpt_B_mix] epoch 2/5 loss=0.0625 devF1=0.9288
[/content/ckpt_B_mix] epoch 3/5 loss=0.0589 devF1=0.9337
[/content/ckpt_B_mix] epoch 4/5 loss=0.0565 devF1=0.9360
[/content/ckpt_B_mix] epoch 5/5 loss=0.0549 devF1=0.9342


Здесь перебираются разные значения tau (от 0.36 до 0.84 с шагом 0.02) и для каждого считается средний F1 на части dev-набора.

* tau — порог вероятности, выше которого модель вставляет пробел.

* best_tau — значение порога, при котором достигается лучший F1.

In [17]:
best_tau, best_f1 = None, -1.0
for tau in [x/100 for x in range(36, 65, 2)]:
    f1 = np.mean([
        f1_pair(positions_from_spaced(predict_spaces(model, src, vocab, tau)),
                positions_from_spaced(tgt))
        for src, tgt in dev_avito[:5000]
    ])
    print(f"tau={tau:.2f} F1_dev={f1:.4f}")
    if f1 > best_f1:
        best_f1, best_tau = f1, tau

print("Best τ:", best_tau, "F1_dev:", best_f1)

tau=0.36 F1_dev=0.9171
tau=0.38 F1_dev=0.9230
tau=0.40 F1_dev=0.9276
tau=0.42 F1_dev=0.9307
tau=0.44 F1_dev=0.9330
tau=0.46 F1_dev=0.9344
tau=0.48 F1_dev=0.9357
tau=0.50 F1_dev=0.9367
tau=0.52 F1_dev=0.9375
tau=0.54 F1_dev=0.9381
tau=0.56 F1_dev=0.9390
tau=0.58 F1_dev=0.9398
tau=0.60 F1_dev=0.9405
tau=0.62 F1_dev=0.9410
tau=0.64 F1_dev=0.9416
Best τ: 0.64 F1_dev: 0.941557806490378


In [20]:
best_tau, best_f1 = None, -1.0
for tau in [x/100 for x in range(60, 75, 2)]:
    f1 = np.mean([
        f1_pair(positions_from_spaced(predict_spaces(model, src, vocab, tau)),
                positions_from_spaced(tgt))
        for src, tgt in dev_avito[:5000]
    ])
    print(f"tau={tau:.2f} F1_dev={f1:.4f}")
    if f1 > best_f1:
        best_f1, best_tau = f1, tau

print("Best τ:", best_tau, "F1_dev:", best_f1)

tau=0.60 F1_dev=0.9405
tau=0.62 F1_dev=0.9410
tau=0.64 F1_dev=0.9416
tau=0.66 F1_dev=0.9423
tau=0.68 F1_dev=0.9428
tau=0.70 F1_dev=0.9437
tau=0.72 F1_dev=0.9442
tau=0.74 F1_dev=0.9446
Best τ: 0.74 F1_dev: 0.9445827602468038


In [21]:
best_tau, best_f1 = None, -1.0
for tau in [x/100 for x in range(74, 85, 2)]:
    f1 = np.mean([
        f1_pair(positions_from_spaced(predict_spaces(model, src, vocab, tau)),
                positions_from_spaced(tgt))
        for src, tgt in dev_avito[:5000]
    ])
    print(f"tau={tau:.2f} F1_dev={f1:.4f}")
    if f1 > best_f1:
        best_f1, best_tau = f1, tau

print("Best τ:", best_tau, "F1_dev:", best_f1)

tau=0.74 F1_dev=0.9446
tau=0.76 F1_dev=0.9450
tau=0.78 F1_dev=0.9452
tau=0.80 F1_dev=0.9455
tau=0.82 F1_dev=0.9457
tau=0.84 F1_dev=0.9456
Best τ: 0.82 F1_dev: 0.9457252674882122


Финальная оценка и сохранение модели

Оценка: на части тестового набора считаем средний F1 с оптимальным tau → получаем итоговое качество модели.

Сохранение: сохраняем словарь весов state_dict, сам словарь символов vocab и подобранный порог tau в файл final_charseg_bundle.pt.

In [22]:
f1_test = np.mean([
    f1_pair(positions_from_spaced(predict_spaces(model, src, vocab, best_tau)),
            positions_from_spaced(tgt))
    for src, tgt in test_avito[:5000]
])
print("Final F1 on test (subset):", f1_test)

torch.save({"state_dict": model.state_dict(), "vocab": vocab, "tau": float(best_tau)},
           "final_charseg_bundle.pt")

Final F1 on test (subset): 0.9459698975688687


### Предсказание на тестовом файле и получение результатов

read_task_file — читает входной файл задачи (id,text_no_spaces) и превращает его в DataFrame.

predict_with_postprocess — для каждого текста:

* восстанавливает пробелы с моделью (predict_spaces),

* прогоняет результат через постпроцессинг (postprocess_text),

* сохраняет список позиций пробелов и финальный текст.

In [23]:
def read_task_file(path):
    rows = []
    with open(path, "r", encoding="utf-8") as f:
        header = f.readline().strip()  # id,text_no_spaces
        for line in f:
            line = line.rstrip("\n")
            if not line:
                continue
            id_str, text = line.split(",", 1)
            rows.append({"id": int(id_str), "text_no_spaces": text})
    return pd.DataFrame(rows, columns=["id", "text_no_spaces"])

@torch.no_grad()
def predict_with_postprocess(model, texts_no_space, vocab, tau):
    model.eval()
    results = []; results_text = []
    for t in texts_no_space:
        spaced = predict_spaces(model, t, vocab, tau=tau)
        cleaned = postprocess_text(spaced)
        results.append(positions_from_spaced(cleaned))
        results_text.append(cleaned)
    return results, results_text


task_path = "/content/dataset_1937770_3.txt"
task_data = read_task_file(task_path)
positions, texts = predict_with_postprocess(model, task_data["text_no_spaces"].astype(str).tolist(), vocab=vocab, tau=best_tau)
task_data["predicted_positions"] = positions
task_data["text_with_spaces"] = texts
submission = task_data[["id", "predicted_positions"]].copy()
submission.to_csv("submission.csv", index=False)
display(task_data.head(20))

id                    text_no_spaces  predicted_positions  \
0    0                   куплюайфон14про          [5, 10, 12]   
1    1                ищудомвПодмосковье            [3, 6, 7]   
2    2     сдаюквартирусмебельюитехникой  [4, 12, 13, 20, 21]   
3    3        новыйдивандоставканедорого          [5, 10, 18]   
4    4                   отдамдаромкошку              [5, 10]   
5    5             работавМосквеудаленно              [7, 13]   
6    6             куплютелевизорPhilips              [5, 14]   
7    7           ищугрузчиковдляпереезда          [3, 12, 15]   
8    8              ремонтквартирподключ          [6, 13, 16]   
9    9                    куплюноутбукHP              [5, 12]   
10  10                 ищуквартирууметро          [3, 11, 12]   
11  11         новаямикроволновкаSamsung              [5, 18]   
12  12             срочнопродамвелосипед              [6, 12]   
13  13                 куплюгитаруFender              [5, 11]   
14  14           ищурепетиторапобиологии          [3, 13, 15]   
15  15         сдаюгаражнадлительныйсрок          [4, 11, 21]   
16  16                      куплюдиванбу              [5, 10]   
17  17  ищумастерапоремонтухолодильников      [3, 10, 12, 19]   
18  18          новыйшкафдоставкасегодня           [5, 9, 17]   
19  19                      куплюXboxOne               [5, 9]   

                        text_with_spaces  
0                     куплю айфон 14 про  
1                  ищу дом в Подмосковье  
2     сдаю квартиру с мебелью и техникой  
3          новый диван доставка недорого  
4                      отдам даром кошку  
5                работав Москве удаленно  
6                куплю телевизор philips  
7             ищу грузчиков для переезда  
8                ремонт квартир под ключ  
9                       куплю ноутбук hp  
10                  ищу квартиру у метро  
11           новая микроволновка samsung  
12               срочно продам велосипед  
13                   куплю гитару Fender  
14            ищу репетитора по биологии  
15          сдаю гаражна длительный срок  
16                       куплю диван б/у  
17  ищу мастера по ремонту холодильников  
18           новый шкаф доставка сегодня  
19                        куплю xbox One

In [25]:
display(task_data.head(100))

id                    text_no_spaces  predicted_positions  \
0    0                   куплюайфон14про          [5, 10, 12]   
1    1                ищудомвПодмосковье            [3, 6, 7]   
2    2     сдаюквартирусмебельюитехникой  [4, 12, 13, 20, 21]   
3    3        новыйдивандоставканедорого          [5, 10, 18]   
4    4                   отдамдаромкошку              [5, 10]   
..  ..                               ...                  ...   
95  95                  ищустудиюнамесяц           [3, 9, 11]   
96  96        новаямикроволновкадоставка              [5, 18]   
97  97               ищуработунавыходные           [3, 9, 11]   
98  98                куплютелефонHuawei              [5, 12]   
99  99  продамшкаф,почтиновый,сзеркалами  [6, 11, 16, 22, 23]   

                         text_with_spaces  
0                      куплю айфон 14 про  
1                   ищу дом в Подмосковье  
2      сдаю квартиру с мебелью и техникой  
3           новый диван доставка недорого  
4                       отдам даром кошку  
..                                    ...  
95                    ищу студию на месяц  
96           новая микроволновка доставка  
97                 ищу работу на выходные  
98                   куплю телефон huawei  
99  продам шкаф, почти новый, с зеркалами  

[100 rows x 4 columns]

In [26]:
task_data.to_csv("task_data.csv", index=False)